In [8]:
import find_equation_id
import subprocess
import time
MACE4 = "LADR-2009-11A/bin/mace4"

In [9]:
def searchcountermodel(assumptions,goals,timelimit,extraclauses="",selection_measure=3,skolems_last="set(skolems_last).",
                     max_megs=2000,max_models = 1, start_size=2,end_size=-1,increment=1,iterate="all",time_per_size=-1,verbose=False):
#Checks with Mace4 if there is a model satisfying eqclause1 & eqclause2 but not eqgoal, with defined time limit and selection measure
    task = rf"""
    assign(max_seconds, {timelimit}).
    assign(max_seconds_per, {time_per_size}).
    assign(start_size, {start_size}).
    assign(end_size, {end_size}).
    assign(increment, {increment}).
    assign(iterate, {iterate}).
    assign(max_megs, {max_megs}).
    assign(max_models,{max_models}).
    assign(selection_measure, {selection_measure}).
    formulas(sos). {assumptions} end_of_list.
    formulas(goals). {goals} end_of_list."""
    mace4_res = subprocess.run(MACE4, input=task, text=True, capture_output=True)
    mace4_out = mace4_res.stdout
    exitcode = mace4_res.returncode
    if verbose: print(f"Exit code:{exitcode}, message:{mace4_res.stderr}")
    if exitcode==0:
        if verbose:
            if "(all_models)" in str(mace4_out):
                print("all models found")
                return (True,f"{max_models} models found")
            else: return True
        else: return True
    elif exitcode==3:
        if verbose:
            return (True,f"Search exhausted before finding {max_models} models")
        else: return True
    elif exitcode==4:
        if verbose:
            return (True,f"Time limit reached before finding {max_models} models")
        else: return True   
    elif exitcode==2:
        if verbose:
            return (False,"Search exhausted")
        else: return False
    elif exitcode==5:
        if verbose:
            return (False,"Time limit reached without finding any models")
        else: return False
    elif exitcode==1:
        if verbose:
            return (False, "error")
        else: return None

In [10]:
def gap2sage(gapgroup):
    G = gap.Image(gap.IsomorphismPermGroup(gapgroup))
    return PermutationGroup(gap_group = G)

In [11]:
def modelfromgroup(G):
    T = G.cayley_table('digits')
    model=T.table()
    return model
def inverses(group):
    invs = []
    elmnts = list(group)
    for g in group:
        inv=elmnts.index(g.inverse())
        invs.append(inv)
    return invs

In [12]:
def translategroup(group,label): #Translation to Mace4 format with operation written as *. groups is a list of groups
    ss=""
    model=modelfromgroup(group)
    size=len(model[0])
    s=f"%{label}\n"
    for i in range(0,size):
        for j in range(0,size):
            s=s+f"""{i}*{j} = {model[i][j]}.
"""
    invs = inverses(group)
    for i,e in enumerate(invs):
            s=s+f"""inv({i}) = {e}.
"""
    ss=ss+s
    return ss[:len(ss)-1] #We remove the last carriage return

In [22]:
def search_countermodel_677_anti_255_translation_invariant_all_groups(orders,verbose=True,return_times=True):
    times={}
    time_start=time.time()
    count=0
    for order in orders:
        time_order=time.time()
        N=Integer(gap.NrSmallGroups(order))
        if verbose: print(f"There are {N} groups of order {order}")
        for groupid in range(1,N+1):
            H=gap.SmallGroup(order,groupid)
            G=gap2sage(H)
            label = gap.StructureDescription(H)
            if verbose: print(f"Checking group {label}")
            time1=time.time()
            assumptions = translategroup(G,label)
            assumptions = assumptions + "\nx=f(f(f(f(x))))."
            assumptions = assumptions + "\nx = f(x * f((inv(x) * f(x)) * f(inv(f(x))))). \nx = f(x)*f((inv(f(x))*f(f(x)))*f(inv(f(f(x)))))."
            goals = "0 = f(0)*(f(inv(f(0)))*f(inv(f(inv(f(0))))*inv(f(0))))."
            res = searchcountermodel(assumptions,goals,-1,extraclauses="",selection_measure=3,skolems_last="",
                     max_megs=10000,start_size=order,end_size=order,verbose=True)
            count += 1
            time2=time.time()
            timeelapsed = round((time2-time1)/60,2)
            times[label]=timeelapsed
            print(f"Group {label} evaluated in {timeelapsed}min. {count} groups evaluated in total.")
            if res[0]:
                print(f"Countermodel found with group {label}!")
                time_end = time.time()
                timeelapsed = round((time_end-time_start)/60,2)
                print(f"Search finished with success in {timeelapsed}min.")
                if return_times:
                    return (G,order,groupid, times)
                return (G,order,groupid)
        time_order_end = time.time()
        timeelapsed = round((time_order_end-time_order)/60,2)
        print(f"\nOrder {order} evaluated in {timeelapsed}min. {N} groups evaluated in this order.")
    time_end = time.time()
    timeelapsed = round((time_end-time_start)/60,2)
    print(f"Search finished without success in {timeelapsed}min.")
    if return_times: return (False,times)
    return False

In [ ]:
search_countermodel_677_anti_255_translation_invariant_all_groups(range(32,33),verbose=True)

There are 51 groups of order 32
Checking group C32


In [ ]:
search_countermodel_677_anti_255_translation_invariant_all_groups(range(33,34),verbose=True)